<a id='0.1'></a>
## 0.1 load required packages

[back to top](#top)

In [1]:
%run "..\..\Startup_py3.py"
sys.path.append(r"..\..\..\..\Documents")

import ImageAnalysis3 as ia
%matplotlib notebook

from ImageAnalysis3 import *
print(os.getpid())

# library design specific tools
from ImageAnalysis3.library_tools import LibraryDesigner as ld
from ImageAnalysis3.library_tools import LibraryTools as lt
# biopython imports
from Bio import SeqIO
from Bio.Seq import Seq
from Bio.SeqRecord import SeqRecord
from Bio.Blast.Applications import NcbiblastnCommandline
from Bio.Blast import NCBIXML

28992


<a id='0.2'></a>
## 0.2 required parameters for Genome

[back to top](#top)

In [2]:
# NEW mouse genome
genome_assembly = 'GRCm39'
reference_folder = os.path.join(r'\\10.245.74.212\Chromatin_NAS_2\Chromatin_Libraries\Genomes\mouse', f'{genome_assembly}_ensembl')
genome_folder = os.path.join(reference_folder, 'Genome')
transcriptome_folder = os.path.join(reference_folder, 'Transcriptome')

In [3]:
class OTTable (dict):
    '''A python dictionary based implementation of the off-target table.'''
    def __missing__ (self, key):
        return 0

    def add_seq(self, seq, weight):
        '''Add a sequence to the OTTable with a given weight.'''
        self[seq] = self[seq] + weight

    def save_pkl(self, file_name):
        '''Save the OTTable as a pickle file.'''
        with open(file_name, 'wb') as f:
            pickle.dump(self, f, pickle.HIGHEST_PROTOCOL)
        print(f'Wrote the OTTable to {file_name}.')
    
    @staticmethod
    def load_pkl(file_name):
        '''Load a OTTable from a pickle file.'''
        with open(file_name, 'rb') as f:
            ottable = pickle.load(f)
        print(f'Load the OTTable from {file_name}.')
        return ottable

In [4]:
from seqint import seq2Int,seq2Int_rc
from tqdm import tqdm
import pickle
Default_Num_Threads=12

class countTable(dict):
    '''A python dictionary based implementation of the off-target table.'''
    def __init__(self, word_len=17, save_file=None, verbose=True):
        # internalize parameters
        self.word_len = word_len
        self.save_file = save_file
        self.verbose = verbose
        super().__init__()
        return
    def __missing__ (self, key):
        return 0
    # function to append sequence
    def add_seq(self, seq, weight):
        '''Add a sequence to the OTTable with a given weight.'''
        self[seq] = self[seq] + weight
    # function 
    def save_pkl(self, file_name=None):
        '''Save the OTTable as a pickle file.'''
        if file_name is None:
            file_name = self.save_file
        with open(file_name, 'wb') as f:
            pickle.dump(self, f, pickle.HIGHEST_PROTOCOL)
        print(f'Wrote the OTTable to {file_name}.')
    def load_sequences(
        self, sequences:list, word_len:int=0, weights:list=[],
        ):
        if self.verbose:
            print(f"Loading {len(sequences)} sequences into count_table.")
        if word_len <= 0 or word_len is None:
            word_len = self.word_len
            if self.verbose:
                print(f"- Use reference word length: {word_len}")
        else:
            if self.verbose:
                print(f"- Use given word length: {word_len}")
        # weights, if applicable
        # Use uniform weights if no weights are given
        if len(weights) == 0:
            weights = [1] * len(sequences)
        assert(len(weights) == len(sequences))
        # load
        for _seq, _w in tqdm(zip(sequences, weights)):
            if len(_seq) < word_len:
                continue
            # Find all K-mers and add to the OTTable
            for j in range(len(_seq) - word_len + 1): 
                self.add_seq(seq2Int(_seq[j:j+word_len].encode()), _w)
        
    #@staticmethod
    def load_pkl(self, save_file=None):
        '''Load a OTTable from a pickle file.'''
        if save_file is None:
            save_file = self.save_file
        with open(save_file, 'rb') as f:
            _saved_table = pickle.load(f)
        print(f'Load the OTTable from {save_file}.')
        # update
        self.update(_saved_table)
        print(f'updated the OTTable from {save_file}.')
        
    
    def get(self,
            query_seq:str, # input sequences as string
            rc:bool=False, # whether reverse-complement
           ):
        """Query of sequences """
        if len(query_seq) < self.word_len:
            return 0
        if rc:
            _seq_counts = [self[seq2Int_rc(query_seq[_i:_i+self.word_len].encode())]
                           for _i in range(len(query_seq)-self.word_len+1)]
        else:
            _seq_counts = [self[seq2Int(query_seq[_i:_i+self.word_len].encode())]
                           for _i in range(len(query_seq)-self.word_len+1)]
        return np.sum(_seq_counts)

In [5]:
# load all ref sequences
from ImageAnalysis3 import library_tools
seq_rd = library_tools.sequences.sequence_reader(transcriptome_folder, auto_load_ref=True)
transcriptome_seqs = [str(_r.seq) for _r in seq_rd.ref_seq_dict.values()]

-- load sequence: ENSMUST00000178537.2, size=12
-- load sequence: ENSMUST00000178862.2, size=14
-- load sequence: ENSMUST00000196221.2, size=9
-- load sequence: ENSMUST00000179664.2, size=11
-- load sequence: ENSMUST00000177564.2, size=16
-- load sequence: ENSMUST00000179520.2, size=11
-- load sequence: ENSMUST00000179883.2, size=16
-- load sequence: ENSMUST00000195858.2, size=10
-- load sequence: ENSMUST00000179932.2, size=12
-- load sequence: ENSMUST00000180001.2, size=17
-- load sequence: ENSMUST00000178815.2, size=10
-- load sequence: ENSMUST00000177965.2, size=17
-- load sequence: ENSMUST00000178909.2, size=29
-- load sequence: ENSMUST00000177646.2, size=10
-- load sequence: ENSMUST00000178230.2, size=17
-- load sequence: ENSMUST00000178483.2, size=29
-- load sequence: ENSMUST00000179262.2, size=10
-- load sequence: ENSMUST00000178549.2, size=17
-- load sequence: ENSMUST00000193012.2, size=29
-- load sequence: ENSMUST00000179166.2, size=10
-- load sequence: ENSMUST00000179560.2, s

-- load sequence: ENSMUST00000099761.10, size=8794
-- load sequence: ENSMUST00000187185.2, size=500
-- load sequence: ENSMUST00000145951.8, size=634
-- load sequence: ENSMUST00000133853.3, size=456
-- load sequence: ENSMUST00000177768.3, size=3922
-- load sequence: ENSMUST00000177289.9, size=3066
-- load sequence: ENSMUST00000110249.3, size=2682
-- load sequence: ENSMUST00000191324.2, size=1593
-- load sequence: ENSMUST00000221003.2, size=728
-- load sequence: ENSMUST00000167565.3, size=3968
-- load sequence: ENSMUST00000165561.4, size=4483
-- load sequence: ENSMUST00000221549.2, size=502
-- load sequence: ENSMUST00000170060.4, size=3723
-- load sequence: ENSMUST00000222460.2, size=2385
-- load sequence: ENSMUST00000074072.5, size=561
-- load sequence: ENSMUST00000163881.2, size=72
-- load sequence: ENSMUST00000133454.8, size=4845
-- load sequence: ENSMUST00000147759.8, size=4972
-- load sequence: ENSMUST00000130671.8, size=4945
-- load sequence: ENSMUST00000100167.10, size=6792
-- loa

-- load sequence: ENSMUST00000163869.2, size=1467
-- load sequence: ENSMUST00000228092.2, size=2790
-- load sequence: ENSMUST00000072972.5, size=1048
-- load sequence: ENSMUST00000228802.2, size=7448
-- load sequence: ENSMUST00000228389.2, size=10213
-- load sequence: ENSMUST00000227317.2, size=8838
-- load sequence: ENSMUST00000080253.5, size=1059
-- load sequence: ENSMUST00000072113.6, size=3747
-- load sequence: ENSMUST00000226578.2, size=3247
-- load sequence: ENSMUST00000228656.2, size=9767
-- load sequence: ENSMUST00000227110.2, size=9888
-- load sequence: ENSMUST00000091721.3, size=897
-- load sequence: ENSMUST00000199318.2, size=2255
-- load sequence: ENSMUST00000204980.3, size=401
-- load sequence: ENSMUST00000204913.3, size=689
-- load sequence: ENSMUST00000199678.4, size=935
-- load sequence: ENSMUST00000203883.3, size=881
-- load sequence: ENSMUST00000204548.2, size=787
-- load sequence: ENSMUST00000196799.2, size=1648
-- load sequence: ENSMUST00000191506.8, size=1132
-- lo

-- load sequence: ENSMUST00000226299.2, size=3729
-- load sequence: ENSMUST00000227971.2, size=496
-- load sequence: ENSMUST00000228784.2, size=376
-- load sequence: ENSMUST00000042988.7, size=3450
-- load sequence: ENSMUST00000091701.3, size=534
-- load sequence: ENSMUST00000055770.4, size=741
-- load sequence: ENSMUST00000038523.15, size=3069
-- load sequence: ENSMUST00000214693.2, size=834
-- load sequence: ENSMUST00000095385.5, size=2909
-- load sequence: ENSMUST00000217175.2, size=2512
-- load sequence: ENSMUST00000214820.2, size=3516
-- load sequence: ENSMUST00000168033.3, size=8228
-- load sequence: ENSMUST00000234051.2, size=13307
-- load sequence: ENSMUST00000234738.2, size=9798
-- load sequence: ENSMUST00000234493.2, size=11539
-- load sequence: ENSMUST00000054425.7, size=481
-- load sequence: ENSMUST00000226039.2, size=1999
-- load sequence: ENSMUST00000223911.2, size=1457
-- load sequence: ENSMUST00000074067.4, size=1480
-- load sequence: ENSMUST00000113251.10, size=2077
--

-- load sequence: ENSMUST00000143937.2, size=485
-- load sequence: ENSMUST00000125572.2, size=600
-- load sequence: ENSMUST00000151389.2, size=547
-- load sequence: ENSMUST00000147306.2, size=639
-- load sequence: ENSMUST00000135355.2, size=417
-- load sequence: ENSMUST00000115188.9, size=1053
-- load sequence: ENSMUST00000123851.8, size=655
-- load sequence: ENSMUST00000151387.2, size=477
-- load sequence: ENSMUST00000115189.10, size=648
-- load sequence: ENSMUST00000099153.10, size=9661
-- load sequence: ENSMUST00000199523.2, size=696
-- load sequence: ENSMUST00000200559.2, size=680
-- load sequence: ENSMUST00000196139.5, size=740
-- load sequence: ENSMUST00000200271.5, size=2724
-- load sequence: ENSMUST00000198529.5, size=1294
-- load sequence: ENSMUST00000199222.5, size=2438
-- load sequence: ENSMUST00000117915.8, size=4913
-- load sequence: ENSMUST00000108210.9, size=2684
-- load sequence: ENSMUST00000196975.5, size=1711
-- load sequence: ENSMUST00000196369.2, size=1666
-- load s

...

-- load sequence: ENSMUST00000150623.2, size=743
-- load sequence: ENSMUST00000204449.3, size=1740
-- load sequence: ENSMUST00000181121.8, size=2142
-- load sequence: ENSMUST00000205093.3, size=873
-- load sequence: ENSMUST00000181840.4, size=995
-- load sequence: ENSMUST00000181145.8, size=2968
-- load sequence: ENSMUST00000204609.2, size=1294
-- load sequence: ENSMUST00000160992.8, size=614
-- load sequence: ENSMUST00000162651.2, size=420
-- load sequence: ENSMUST00000162829.2, size=435
-- load sequence: ENSMUST00000207056.2, size=504
-- load sequence: ENSMUST00000203711.2, size=172
-- load sequence: ENSMUST00000147939.2, size=625
-- load sequence: ENSMUST00000162276.10, size=392
-- load sequence: ENSMUST00000161923.2, size=2425
-- load sequence: ENSMUST00000161282.2, size=184
-- load sequence: ENSMUST00000187956.2, size=775
-- load sequence: ENSMUST00000161449.2, size=2405
-- load sequence: ENSMUST00000133752.2, size=1493
-- load sequence: ENSMUST00000211790.2, size=1382
-- load seq

-- load sequence: ENSMUST00000181369.2, size=501
-- load sequence: ENSMUST00000238088.2, size=520
-- load sequence: ENSMUST00000226503.2, size=1412
-- load sequence: ENSMUST00000174283.2, size=2210
-- load sequence: ENSMUST00000181951.2, size=3467
-- load sequence: ENSMUST00000220061.2, size=654
-- load sequence: ENSMUST00000219459.2, size=1303
-- load sequence: ENSMUST00000197430.2, size=424
-- load sequence: ENSMUST00000200648.2, size=1957
-- load sequence: ENSMUST00000141700.2, size=2231
-- load sequence: ENSMUST00000196770.2, size=4352
-- load sequence: ENSMUST00000197309.2, size=3463
-- load sequence: ENSMUST00000153208.2, size=948
-- load sequence: ENSMUST00000237543.2, size=1053
-- load sequence: ENSMUST00000236278.2, size=971
-- load sequence: ENSMUST00000237768.2, size=589
-- load sequence: ENSMUST00000237231.2, size=1771
-- load sequence: ENSMUST00000235456.2, size=1130
-- load sequence: ENSMUST00000235897.2, size=661
-- load sequence: ENSMUST00000236069.2, size=969
-- load s

-- load sequence: ENSMUST00000182497.2, size=2929
-- load sequence: ENSMUST00000230620.2, size=344
-- load sequence: ENSMUST00000218979.2, size=267
-- load sequence: ENSMUST00000177492.2, size=1131
-- load sequence: ENSMUST00000227115.2, size=568
-- load sequence: ENSMUST00000226371.2, size=1072
-- load sequence: ENSMUST00000228838.2, size=1418
-- load sequence: ENSMUST00000227517.2, size=811
-- load sequence: ENSMUST00000177065.2, size=698
-- load sequence: ENSMUST00000217771.2, size=3607
-- load sequence: ENSMUST00000176406.2, size=587
-- load sequence: ENSMUST00000218793.2, size=529
-- load sequence: ENSMUST00000220015.2, size=172
-- load sequence: ENSMUST00000219252.2, size=338
-- load sequence: ENSMUST00000210723.2, size=459
-- load sequence: ENSMUST00000211274.2, size=483
-- load sequence: ENSMUST00000209312.2, size=1621
-- load sequence: ENSMUST00000218657.2, size=1864
-- load sequence: ENSMUST00000144990.2, size=469
-- load sequence: ENSMUST00000227020.2, size=741
-- load seque

-- load sequence: ENSMUST00000201375.2, size=1133
-- load sequence: ENSMUST00000124811.2, size=384
-- load sequence: ENSMUST00000123644.3, size=1172
-- load sequence: ENSMUST00000145534.2, size=350
-- load sequence: ENSMUST00000215849.2, size=798
-- load sequence: ENSMUST00000181712.3, size=1581
-- load sequence: ENSMUST00000215242.2, size=2102
-- load sequence: ENSMUST00000217385.2, size=1782
-- load sequence: ENSMUST00000215349.2, size=299
-- load sequence: ENSMUST00000213885.2, size=619
-- load sequence: ENSMUST00000214913.2, size=914
-- load sequence: ENSMUST00000217145.2, size=373
-- load sequence: ENSMUST00000213920.2, size=999
-- load sequence: ENSMUST00000214085.2, size=721
-- load sequence: ENSMUST00000144193.2, size=271
-- load sequence: ENSMUST00000217323.2, size=269
-- load sequence: ENSMUST00000214727.2, size=538
-- load sequence: ENSMUST00000191396.2, size=1009
-- load sequence: ENSMUST00000217349.2, size=3869
-- load sequence: ENSMUST00000213995.2, size=722
-- load seque

-- load sequence: ENSMUST00000207045.2, size=2094
-- load sequence: ENSMUST00000207829.2, size=549
-- load sequence: ENSMUST00000149300.8, size=1492
-- load sequence: ENSMUST00000156387.2, size=749
-- load sequence: ENSMUST00000144728.2, size=992
-- load sequence: ENSMUST00000145972.8, size=676
-- load sequence: ENSMUST00000067618.5, size=1780
-- load sequence: ENSMUST00000166653.2, size=309
-- load sequence: ENSMUST00000131099.2, size=2959
-- load sequence: ENSMUST00000149285.2, size=733
-- load sequence: ENSMUST00000143202.8, size=1928
-- load sequence: ENSMUST00000135739.2, size=1854
-- load sequence: ENSMUST00000141452.2, size=3387
-- load sequence: ENSMUST00000141473.2, size=626
-- load sequence: ENSMUST00000129485.2, size=126
-- load sequence: ENSMUST00000150616.2, size=403
-- load sequence: ENSMUST00000201816.2, size=1292
-- load sequence: ENSMUST00000210851.2, size=1148
-- load sequence: ENSMUST00000209947.2, size=1032
-- load sequence: ENSMUST00000211430.2, size=1193
-- load s

In [6]:
transcriptome_savefile = os.path.join(r'D:\References', f"{genome_assembly}_transcriptome_table.pkl")
if os.path.isfile(transcriptome_savefile):
    print(f"Loading transcriptome table file")
    transcriptome_table = countTable()
    transcriptome_table.load_pkl(transcriptome_savefile)
else:
    # process
    transcriptome_table = countTable()
    transcriptome_table.load_sequences(transcriptome_seqs)
    print(f"Save transcriptome table to file: {transcriptome_savefile}")
    transcriptome_table.save_pkl(transcriptome_savefile)

Loading transcriptome table file
Load the OTTable from D:\References\GRCm39_transcriptome_table.pkl.
updated the OTTable from D:\References\GRCm39_transcriptome_table.pkl.


In [7]:
# json
import json

In [15]:
%%time
transcriptome_savefile = os.path.join(r'D:\References', f"{genome_assembly}_transcriptome_table.npy")
np.save(transcriptome_savefile, transcriptome_table)

Wall time: 11.6 s


In [16]:
%%time
test_ct = np.load(transcriptome_savefile, allow_pickle=True)

Wall time: 55.8 s


In [19]:
%%time
test_array = np.array([list(transcriptome_table.keys()), list(transcriptome_table.values())], dtype=np.uint64)

Wall time: 12.1 s


In [22]:
%%time
transcriptome_savefile = os.path.join(r'D:\References', f"{genome_assembly}_transcriptome_table_test.npy")
np.save(transcriptome_savefile, test_array)

Wall time: 4.58 s


In [26]:
%%time
test_ct = np.load(transcriptome_savefile, allow_pickle=True)

Wall time: 538 ms


In [30]:
test_ct[0,-1] == test_array[0,-1]

True

In [34]:
test_table = countTable()
for _k, _v in tqdm(zip(test_ct[0], test_ct[1])):
    test_table[int(_k)] = int(_v)

110282344it [02:15, 812678.35it/s]


In [32]:
np.unique(test_ct[0] - test_array[0])

array([0], dtype=uint64)

In [24]:
test_ct.shape

(2, 110282344)

In [7]:
transcriptome_table = countTable()
transcriptome_table.load_sequences(transcriptome_seqs)

Loading 139145 sequences into count_table.
- Use reference word length: 17


139145it [03:40, 629.93it/s] 


In [9]:
transcriptome_savefile = os.path.join(r'D:\References', f"{genome_assembly}_transcriptome_table.pkl")
if os.path.isfile(transcriptome_savefile):
    print(f"transcriptome table file already exist, skip.")
else:
    print(f"Save transcriptome table to file: {transcriptome_savefile}")
    transcriptome_table.save_pkl(transcriptome_savefile)

Save transcriptome table to file: D:\References\GRCm39_transcriptome_table.pkl
Wrote the OTTable to D:\References\GRCm39_transcriptome_table.pkl.


In [50]:
genome_savefile = os.path.join(r'D:\References', f"{genome_assembly}_genome_table.pkl")

In [ ]:
genome_savefile = os.path.join(r'D:\References', f"{genome_assembly}_genome_table.pkl")
if os.path.isfile(genome_savefile):
    print(f"genome table file already exist, skip.")
else:
    print(f"Save genome table to file: {genome_savefile}")
    genome_table.save_pkl(genome_savefile)

In [10]:
%%time
test_ct = countTable()
test_ct.load_pkl(transcriptome_savefile)

Load the OTTable from D:\References\GRCm39_transcriptome_table.pkl.
updated the OTTable from D:\References\GRCm39_transcriptome_table.pkl.
Wall time: 1min 7s


In [12]:
type(test_ct)

__main__.countTable

In [14]:
%%timeit
test_ct.get(transcriptome_seqs[50][:17], )

7.61 µs ± 127 ns per loop (mean ± std. dev. of 7 runs, 100000 loops each)


In [13]:
test_ct.get?

In [51]:
%%time
genome_ct = countTable()
genome_ct.load_pkl(genome_savefile)

Load the OTTable from D:\References\GRCm39_genome_table.pkl.
updated the OTTable from D:\References\GRCm39_genome_table.pkl.
Wall time: 1h 21min 39s


In [15]:
%%time
genome_savefile = os.path.join(r'D:\References', f"{genome_assembly}_genome_table.pkl")
test_genome_ct = pickle.load(open(genome_savefile, 'rb'))

Wall time: 27min 38s


In [ ]:
test_ge

In [48]:
ctp11_folder = r'\\10.245.74.212\Chromatin_NAS_2\Chromatin_Libraries\CTP-11_brain\mouse_genome_1000'

ctp11_table_file = os.path.join(reference_folder, 'ctp11_genome_17w.npy')
test_ct = ld.countTable(sparse=False, save_file=ctp11_table_file)
test_ct.load()

In [49]:
%%timeit
test_ct.get(transcriptome_seqs[50][:17], )

9.07 µs ± 14.7 ns per loop (mean ± std. dev. of 7 runs, 100000 loops each)


In [41]:
def get(self,
        query_seq:str, # input sequences as string
        rc:bool=False, # whether reverse-complement
       ):
    """Query of sequences """
    if len(query_seq) < self.word_len:
        return 0
    if rc:
        _seq_counts = [self[seq2Int_rc(query_seq[_i:_i+self.word_len].encode())]
                       for _i in range(len(query_seq)-self.word_len+1)]
    else:
        _seq_counts = [self[seq2Int(query_seq[_i:_i+self.word_len].encode())]
                       for _i in range(len(query_seq)-self.word_len+1)]
    print(_seq_counts)
    return np.sum(_seq_counts)

In [42]:
get(test_ct, test_seq)

[2]


2

In [17]:
transcriptome_table[seq2Int(test_seq.encode())]

2

In [18]:
%%timeit
transcriptome_table[seq2Int(test_seq.encode())]

213 ns ± 2.79 ns per loop (mean ± std. dev. of 7 runs, 1000000 loops each)


## Genome

In [35]:
# load all ref sequences
from ImageAnalysis3 import library_tools
seq_rd = library_tools.sequences.sequence_reader(genome_folder, auto_load_ref=True)
genome_seqs = [str(_r.seq) for _r in seq_rd.ref_seq_dict.values()]

-- load sequence: 1, size=195154279
-- load sequence: 10, size=130530862
-- load sequence: 11, size=121973369
-- load sequence: 12, size=120092757
-- load sequence: 13, size=120883175
-- load sequence: 14, size=125139656
-- load sequence: 15, size=104073951
-- load sequence: 16, size=98008968
-- load sequence: 17, size=95294699
-- load sequence: 18, size=90720763
-- load sequence: 19, size=61420004
-- load sequence: 2, size=181755017
-- load sequence: 3, size=159745316
-- load sequence: 4, size=156860686
-- load sequence: 5, size=151758149
-- load sequence: 6, size=149588044
-- load sequence: 7, size=144995196
-- load sequence: 8, size=130127694
-- load sequence: 9, size=124359700
-- load sequence: MT, size=16299
-- load sequence: X, size=169476592
-- load sequence: Y, size=91455967
-- load sequence: JH584299.1, size=953012
-- load sequence: GL456233.2, size=559103
-- load sequence: JH584301.1, size=259875
-- load sequence: GL456211.1, size=241735
-- load sequence: GL456221.1, size=206

In [36]:
%%time
genome_table = countTable()
genome_table.load_sequences(genome_seqs)

Loading 61 sequences into count_table.
- Use reference word length: 17


61it [1:22:33, 81.20s/it] 


Wall time: 1h 22min 34s


In [37]:
%%timeit
genome_table.get(transcriptome_seqs[50][:17], )

7.79 µs ± 84 ns per loop (mean ± std. dev. of 7 runs, 100000 loops each)
Compiler time: 0.23 s


In [38]:
%%time
genome_savefile = os.path.join(r'D:\References', f"{genome_assembly}_genome_table.npy")
if os.path.isfile(genome_savefile):
    print(f"genome table file already exist, skip.")
else:
    print(f"Save genome table to file: {genome_savefile}")
    np.save(genome_savefile, genome_table)

Save genome table to file: D:\References\GRCm39_genome_table.npy
Wall time: 4min 40s


In [43]:
%%time
genome_savefile = os.path.join(r'D:\References', f"{genome_assembly}_genome_table.pkl")
test_ct = pickle.load(open(genome_savefile, 'rb'))

MemoryError: 

In [39]:
%%time
genome_savefile = os.path.join(r'D:\References', f"{genome_assembly}_genome_table.pkl")
if os.path.isfile(genome_savefile):
    print(f"genome table file already exist, skip.")
else:
    print(f"Save genome table to file: {genome_savefile}")
    genome_table.save_pkl(genome_savefile)

Save genome table to file: D:\References\GRCm39_genome_table.pkl
Wrote the OTTable to D:\References\GRCm39_genome_table.pkl.
Wall time: 2min 55s
